In [ ]:
# This cell is mandatory in all Dymos documentation notebooks.
missing_packages = []
try:
    import openmdao.api as om  # noqa: F401
except ImportError:
    if 'google.colab' in str(get_ipython()):
        !python -m pip install openmdao[notebooks]
    else:
        missing_packages.append('openmdao')
try:
    import dymos as dm  # noqa: F401
except ImportError:
    if 'google.colab' in str(get_ipython()):
        !python -m pip install dymos
    else:
        missing_packages.append('dymos')
try:
    import pyoptsparse  # noqa: F401
except ImportError:
    if 'google.colab' in str(get_ipython()):
        !pip install -q condacolab
        import condacolab
        condacolab.install_miniconda()
        !conda install -c conda-forge pyoptsparse
    else:
        missing_packages.append('pyoptsparse')
if missing_packages:
    raise EnvironmentError('This notebook requires the following packages '
                           'please install them and restart this notebook\'s runtime: {",".join(missing_packages)}')

# Timeseries Outputs

Different optimal control transcriptions work in different ways.
The Radau Pseudospectral transcription keeps a contiguous vector of state values at all nodes.
The Gauss Lobatto transcription keeps two separate continuous vectors; one at the discretization nodes and the other at the collocation nodes.
Retrieving a timeseries values of output values is thus transcription dependent.

In order to make obtaining the timeseries output of a phase easier, each phase provides a timeseries component which collects and outputs the appropriate timeseries data.
For the pseudospectral transcriptions, timeseries outputs are provided at all nodes.
By default, the timeseries output will include the following variables for every problem.

## Paths to timeseries outputs in Dymos

|Path                                                          | Description                                         |
|--------------------------------------------------------------|-----------------------------------------------------|
|``<phase path>.timeseries.time``                              |Current time value                                   |
|``<phase path>.timeseries.time_phase``                        |Current phase elapsed time                           |
|``<phase path>.timeseries.<x>``                        |Value of state variable named x                      |
|``<phase path>.timeseries.<u>``                      |Value of control variable named u                    |
|``<phase path>.timeseries.<u>_rate``            |Time derivative of control named u                   |
|``<phase path>.timeseries.<u>_rate2``           |Second time derivative of control named u            |
|``<phase path>.timeseries.<p>``           |Value of polynomial control variable named u         |
|``<phase path>.timeseries.<p>_rate`` |Time derivative of polynomial control named u        |
|``<phase path>.timeseries.<p>_rate2``|Second time derivative of polynomial control named u |
|``<phase path>.timeseries.<d>``                    |Value of parameter named d                           |

## Adding additional timeseries outputs

In addition to these default values, any output of the ODE can be added to the timeseries output
using the ``add_timeseries_output`` method on Phase.  These outputs are available as
``<phase path>.timeseries.<output name>``.  A glob pattern can be used with ``add_timeseries_output``
to add multiple outputs to the timeseries simultaneously.  For instance, just passing '*' as the variable
name will add all dynamic outputs of the ODE to the timeseries.

Dymos will ignore any ODE outputs that are not sized such that the first dimension is the same as the
number of nodes in the ODE.  That is, if the output variable doesn't appear to be dynamic, it will not
be included in the timeseries outputs.

```{eval-rst}
    .. automethod:: dymos.Phase.add_timeseries_output
        :noindex:
```

## Interpolated Timeseries Outputs

Sometimes a user may want to interpolate the results of a phase onto a different grid.  This is particularly
useful in the context of [tandem phases](examples:brachistochrone_tandem_phases).  Additional timeseries may be added to a phase using the ``add_timeseries`` method.  By default all timeseries will provide times, states, controls, and parameters on the specified output grid.  Adding other variables is accomplished using the
``timeseries`` argument in the ``add_timeseries_output`` method.

```{eval-rst}
    .. automethod:: dymos.Phase.add_timeseries
        :noindex:
```